In [1]:
import numpy as np
import pickle as pkl
import pandas as pd 
from gensim.models import LdaModel
import json

In [2]:
nTopics = 25

In [3]:
# Load model
lda_model = LdaModel.load(f'trained_models/trained_lda_model_{nTopics}')

# Load topic distributions
topic_distributions = np.load(f'data/topic_distributions_{lda_model.num_topics}.npy')

# Pull topics
topics = lda_model.show_topics(formatted=False, num_topics=nTopics, num_words=20)

# load raw corpus dataframe
with open('data/raw_corpus.pkl', 'rb') as f:
    corpus_df = pkl.load(f)

In [4]:
#convert all nans to zeros and all zeros to a very small number
# topic_distributions = np.nan_to_num(topic_distributions)
topic_distributions = np.where(topic_distributions == 0, 0.000001, topic_distributions)
# topic_distributions

In [5]:
#calculate JSD for all pairs of papers
#the max force values (dist) are capped to 1000 later on
def calc_KL_divergence(paper1,paper2):
    return -np.nansum(paper1 * np.log(paper2/paper1))
def jensen_shannon_distance(paper1,paper2):
    M=0.5*(paper1+paper2)
    D1=calc_KL_divergence(paper1,M)
    D2=calc_KL_divergence(paper2,M)
    JSDiv = 0.5*D1+0.5*D2
    JSD = np.sqrt(JSDiv)
    return JSD

In [19]:
#Select by year and journal
year_id = input("Insert year of publication: ")
journal_id = input("Insert journal id (options: WRR, HESS, JHM, HSJ, JH, HP): ")
df_year = corpus_df.loc[corpus_df['Year'] == year_id]
df_year_journal = df_year.loc[df_year['Journal'] == journal_id]
df_year_journal

Insert year of publication: :
Insert journal id (options: WRR, HESS, JHM, HSJ, JH, HP): :


Empty DataFrame
Columns: [DOI, Year, Journal, Title, Abstract, Affiliation]
Index: []

In [ ]:
#Select minimum paper correlation cutoff point (use quantiles instead)
# min_cutoff = input("Select minimum paper distance cutoff (Options: High, Medium, Low): ")
# min_cutoff = min_cutoff.lower()

# #Note to self - set quantiles
# if min_cutoff == 'high':
#     cut_val = 2.5
# elif min_cutoff == 'medium':
#     cut_val = 2.0
# elif min_cutoff == 'low':
#     cut_val == 1.5   

In [17]:
topic_distributions[1][:].shape

(25,)

In [ ]:
#initiate individual lists for nodes and links
node_list = []
# link_list = []

    
# for p1, paper1 in enumerate(df_year_journal["Title"][:]):
#     max_topic = np.argmax(topic_distributions[p1])
#     grp = {"group" : max_topic, "name": paper1}
#     node_list.append(grp)
#     for p2, paper2 in enumerate(df_year_journal["Title"][p1:]):
#         if p1 == p2:
#             dist = 0
#         else:
#             JSD = jensen_shannon_distance(topic_distributions[p1, sel_topic], topic_distributions[p2, sel_topic])
#             dist = round(1/JSD, 2)
#             if dist >= 2.0 and dist <= 10:
#                 link = {"source": p1, "target": p2, "value": dist}
#                 link_list.append(link)
#             continue

In [22]:
jsd_arr  = np.array([])
for p1, paper1 in enumerate(corpus_df["Title"][:]):
    for p2, paper2 in enumerate(corpus_df["Title"][p1:]):
        if p1 == p2:
            dist = 0
        else:
            JSD = jensen_shannon_distance(topic_distributions[p1, 1], topic_distributions[p2, 1])
            dist = round(1/JSD, 2)
            jsd_arr = np.append(jsd_arr, dist)
            print(jsd_arr)

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:8: RuntimeWarning: divide by zero encountered in double_scalars
  


[-inf]
[-inf -inf]
[-inf -inf -inf]
[-inf -inf -inf -inf]
[-inf -inf -inf -inf -inf]
[-inf -inf -inf -inf -inf -inf]
[-inf -inf -inf -inf -inf -inf -inf]
[-inf -inf -inf -inf -inf -inf -inf 3.05]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf 7.84]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf 7.84 -inf]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf 7.84 -inf -inf]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf 7.84 -inf -inf -inf]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf 7.84 -inf -inf -inf
 -inf]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf 7.84 -inf -inf -inf
 -inf 4.27]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf 7.84 -inf -inf -inf
 -inf 4.27 -inf]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf 7.84 -inf -inf -inf
 -inf 4.27 -inf -inf]
[-inf -inf -inf -inf -inf -inf -inf 3.05 -inf -inf 7.84 -inf -inf -inf
 -inf 4.27 -inf -inf -inf]
[-inf -

 11.19  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf]
[ -inf  -inf  -inf  -inf  -inf  -inf  -inf  3.05  -inf  -inf  7.84  -inf
  -inf  -inf  -inf  4.27  -inf  -inf  -inf  -inf  -inf  3.2   -inf  -inf
  8.08  4.8   -inf  -inf  -inf  -inf  -inf  -inf  3.2   -inf  -inf  3.11
  5.26  -inf 16.05 10.41  -inf  -inf  -inf  -inf  4.05  -inf  -inf  -inf
  -inf  -inf 10.82  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf
  -inf  -inf  -inf  -inf  2.95  7.11  -inf  -inf  -inf  -inf  -inf  6.29
  -inf  -inf  -inf  -inf 15.62  -inf  2.91  -inf  3.45  -inf  -inf  -inf
  4.17  -inf  -inf  3.77  -inf  -inf  -inf  -inf  -inf  -inf  9.11  -inf
  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf 16.4   -inf  4.28
  -inf  2.61  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf
  -inf  1.98  -inf  -inf  -inf  2.7   -inf  -inf  -inf  2.18  -inf  -inf
  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf 11.63 15.45  -inf  8.36
  -inf  -inf  -inf  -inf  -inf  3.52  -inf  -inf  3.59  -inf 15.18 1

  -inf]
[ -inf  -inf  -inf  -inf  -inf  -inf  -inf  3.05  -inf  -inf  7.84  -inf
  -inf  -inf  -inf  4.27  -inf  -inf  -inf  -inf  -inf  3.2   -inf  -inf
  8.08  4.8   -inf  -inf  -inf  -inf  -inf  -inf  3.2   -inf  -inf  3.11
  5.26  -inf 16.05 10.41  -inf  -inf  -inf  -inf  4.05  -inf  -inf  -inf
  -inf  -inf 10.82  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf
  -inf  -inf  -inf  -inf  2.95  7.11  -inf  -inf  -inf  -inf  -inf  6.29
  -inf  -inf  -inf  -inf 15.62  -inf  2.91  -inf  3.45  -inf  -inf  -inf
  4.17  -inf  -inf  3.77  -inf  -inf  -inf  -inf  -inf  -inf  9.11  -inf
  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf 16.4   -inf  4.28
  -inf  2.61  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf
  -inf  1.98  -inf  -inf  -inf  2.7   -inf  -inf  -inf  2.18  -inf  -inf
  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf 11.63 15.45  -inf  8.36
  -inf  -inf  -inf  -inf  -inf  3.52  -inf  -inf  3.59  -inf 15.18 12.55
  -inf  -inf  -inf  -inf  8.82  -inf  -inf 

[ -inf  -inf  -inf  -inf  -inf  -inf  -inf  3.05  -inf  -inf  7.84  -inf
  -inf  -inf  -inf  4.27  -inf  -inf  -inf  -inf  -inf  3.2   -inf  -inf
  8.08  4.8   -inf  -inf  -inf  -inf  -inf  -inf  3.2   -inf  -inf  3.11
  5.26  -inf 16.05 10.41  -inf  -inf  -inf  -inf  4.05  -inf  -inf  -inf
  -inf  -inf 10.82  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf
  -inf  -inf  -inf  -inf  2.95  7.11  -inf  -inf  -inf  -inf  -inf  6.29
  -inf  -inf  -inf  -inf 15.62  -inf  2.91  -inf  3.45  -inf  -inf  -inf
  4.17  -inf  -inf  3.77  -inf  -inf  -inf  -inf  -inf  -inf  9.11  -inf
  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf 16.4   -inf  4.28
  -inf  2.61  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf
  -inf  1.98  -inf  -inf  -inf  2.7   -inf  -inf  -inf  2.18  -inf  -inf
  -inf  -inf  -inf  -inf  -inf  -inf  -inf  -inf 11.63 15.45  -inf  8.36
  -inf  -inf  -inf  -inf  -inf  3.52  -inf  -inf  3.59  -inf 15.18 12.55
  -inf  -inf  -inf  -inf  8.82  -inf  -inf  -inf  -

...

[-inf -inf -inf ... -inf 4.91 3.71]
[-inf -inf -inf ... 4.91 3.71 5.83]
[-inf -inf -inf ... 3.71 5.83 -inf]
[-inf -inf -inf ... 5.83 -inf 7.32]
[-inf -inf -inf ... -inf 7.32 -inf]
[-inf -inf -inf ... 7.32 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf 4.91]
[-inf -inf -inf ... -inf 4.91 -inf]
[-inf -inf -inf ... 4.91 -inf 3.82]
[-inf -inf -inf ... -inf 3.82 -inf]
[-inf -inf -inf ... 3.82 -inf 2.47]
[-inf -inf -inf ... -inf 2.47 -inf]
[-inf -inf -inf ... 2.47 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf 4.64]
[-inf -inf -inf ... -inf 4.64 -inf]
[-inf -inf -inf ... 4.64 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf 6.91]
[-inf -inf -inf ... -inf 6.91 -inf]
[-inf -inf -inf ... 6.91 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -in

[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf 3.69]
[-inf -inf -inf ... -inf 3.69 -inf]
[-inf -inf -inf ... 3.69 -inf -inf]
[ -inf  -inf  -inf ...  -inf  -inf 12.81]
[ -inf  -inf  -inf ...  -inf 12.81  -inf]
[ -inf  -inf  -inf ... 12.81  -inf  -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf 3.82]
[-inf -inf -inf ... -inf 3.82 -inf]
[-inf -inf -inf ... 3.82 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf  3.3]
[-inf -inf -inf ... -inf  3.3 -inf]
[-inf -inf -inf ... 3.3  -inf 6.52]
[-inf -inf -inf ... -inf 6.52 7.93]
[-inf -inf -inf ... 6.52 7.93 -inf]
[-inf -inf -inf ... 7.93 -inf 2.59]
[-inf -inf -inf ... -inf 2.59 -inf]
[-inf -inf -inf ... 2.59 -inf 8.49]
[-inf -inf -inf ... -inf 8.49 8.49]
[-inf -inf -inf ... 8.49 8.49 8.49]
[-inf -inf -inf ... 8.49 8.49 -inf]
[-inf -inf -inf ... 8.49 -inf -inf]
[-inf -inf

[-inf -inf -inf ... 7.84 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf 4.27]
[-inf -inf -inf ... -inf 4.27 -inf]
[-inf -inf -inf ... 4.27 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf  3.2]
[-inf -inf -inf ... -inf  3.2 -inf]
[-inf -inf -inf ...  3.2 -inf -inf]
[-inf -inf -inf ... -inf -inf 8.08]
[-inf -inf -inf ... -inf 8.08 4.8 ]
[-inf -inf -inf ... 8.08 4.8  -inf]
[-inf -inf -inf ...  4.8 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf  3.2]
[-inf -inf -inf ... -inf  3.2 -inf]
[-inf -inf -inf ...  3.2 -inf -inf]
[-inf -inf -inf ... -inf -inf 3.11]
[-inf -inf -inf ... -inf 3.11 5.26]
[-inf -inf -inf ... 3.11 5.26 -inf]
[ -inf  -inf  -inf ...  5.26  -inf 16.05]
[ -inf  -inf  -inf ...

[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf 4.57]
[-inf -inf -inf ... -inf 4.57 -inf]
[-inf -inf -inf ... 4.57 -inf -inf]
[-inf -inf -inf ... -inf -inf 2.04]
[-inf -inf -inf ... -inf 2.04 2.84]
[-inf -inf -inf ... 2.04 2.84 4.28]
[-inf -inf -inf ... 2.84 4.28 6.13]
[-inf -inf -inf ... 4.28 6.13 -inf]
[-inf -inf -inf ... 6.13 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf  5.2]
[-inf -inf -inf ... -inf 5.2  3.72]
[-inf -inf -inf ... 5.2  3.72 -inf]
[-inf -inf -inf ... 3.72 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf 9.92]
[-inf -inf -inf ... -inf 9.92 -inf]
[-inf -inf -inf ... 9.92 -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -inf -inf]
[-inf -inf -inf ... -inf -in

KeyboardInterrupt: 